In [1]:
import numpy as np
import tensorflow as tf

In [2]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2 and Pooling Layer #2
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Dense Layer
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits Layer
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }

  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [3]:
def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="./mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)

In [4]:
tf.app.run()

Instructions for updating:
Use the retry module or similar alternatives.
Instructions for updating:
Please use tf.data.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': './mnist_convnet_model', '_tf_random_seed': None, 

INFO:tensorflow:loss = 2.2970746, step = 0
INFO:tensorflow:probabilities = [[0.11201016 0.10830699 0.09134892 0.09121045 0.09824633 0.0863217
  0.11549625 0.10440432 0.10699687 0.08565802]
 [0.11220919 0.09395602 0.09426638 0.09925717 0.09863462 0.08420043
  0.11470021 0.1109685  0.09974685 0.09206068]
 [0.09459802 0.09718009 0.10144314 0.1066553  0.1047915  0.08290198
  0.11417212 0.09991319 0.10236143 0.09598325]
 [0.10699883 0.12068017 0.09203532 0.09663571 0.10452096 0.08126685
  0.11189555 0.09162606 0.09527792 0.09906258]
 [0.10558219 0.1039615  0.09886488 0.09633265 0.09904508 0.09048802
  0.10931409 0.09928534 0.10434895 0.09277724]
 [0.10774946 0.0988732  0.10494505 0.08849496 0.10999951 0.08569586
  0.11830146 0.10527845 0.08584905 0.09481303]
 [0.10987283 0.09857693 0.0966424  0.09988897 0.10881815 0.09787907
  0.12159789 0.09000055 0.08894272 0.0877805 ]
 [0.09410762 0.0983171  0.10099958 0.10505189 0.10189414 0.09750047
  0.09977903 0.09898274 0.10751441 0.09585304]
 [0.14

INFO:tensorflow:global_step/sec: 45.895
INFO:tensorflow:probabilities = [[0.09947672 0.10943208 0.10057703 0.10228308 0.10060927 0.09560998
  0.10943189 0.0906282  0.1005196  0.09143222]
 [0.10297094 0.09419466 0.09034748 0.10032459 0.12274455 0.09659433
  0.11210937 0.09085105 0.09717058 0.09269248]
 [0.09755825 0.09494371 0.09281833 0.09441581 0.11270943 0.08809461
  0.12011255 0.101734   0.10795774 0.08965555]
 [0.11321767 0.08931904 0.10222694 0.09950125 0.10643735 0.09920283
  0.1074937  0.08955652 0.09134375 0.10170092]
 [0.09824494 0.10695159 0.09851418 0.09855108 0.10380496 0.09931716
  0.10133529 0.09488595 0.09988877 0.09850612]
 [0.09731597 0.10560038 0.10343031 0.09946512 0.10259879 0.0940441
  0.10871575 0.09700132 0.09365108 0.09817717]
 [0.1061061  0.09665252 0.09117218 0.09505159 0.11946246 0.08077585
  0.11105394 0.11876402 0.09172977 0.0892316 ]
 [0.12597741 0.08231829 0.08747423 0.08867524 0.10485603 0.09216918
  0.09503914 0.11877029 0.09749826 0.10722194]
 [0.10636

INFO:tensorflow:loss = 2.2707615, step = 100 (2.183 sec)
INFO:tensorflow:probabilities = [[0.10536043 0.09872328 0.08829525 0.107621   0.10175118 0.08749466
  0.10852269 0.1035882  0.09882931 0.09981397]
 [0.10647024 0.09628857 0.0895265  0.0954198  0.11901988 0.09127322
  0.10561023 0.09438471 0.10185511 0.10015178]
 [0.10376055 0.09074603 0.09281083 0.10057937 0.10286722 0.0766696
  0.12618786 0.10287485 0.10697431 0.09652939]
 [0.09229799 0.10576202 0.09621761 0.09832818 0.11203634 0.08320203
  0.10116236 0.10007556 0.11572967 0.09518825]
 [0.11505559 0.10148375 0.10198179 0.09511869 0.10322782 0.08658208
  0.11854754 0.09559043 0.09443792 0.08797432]
 [0.11254632 0.09784818 0.09928529 0.09247407 0.10940243 0.08714961
  0.09681341 0.1103938  0.09378928 0.10029765]
 [0.11053263 0.07918206 0.11235239 0.10176003 0.11194676 0.08275921
  0.11347318 0.10272648 0.09039788 0.09486943]
 [0.10953797 0.12396698 0.10421938 0.09671844 0.09592712 0.08208505
  0.10799617 0.09425106 0.09719913 0.08

INFO:tensorflow:global_step/sec: 47.7824
INFO:tensorflow:probabilities = [[0.11015987 0.08489928 0.10538974 0.09555797 0.10755952 0.07966288
  0.10653108 0.10633327 0.09573035 0.1081761 ]
 [0.12263462 0.08989802 0.09583038 0.10947412 0.10133529 0.08197709
  0.1117927  0.10276803 0.09985396 0.08443577]
 [0.09111711 0.10636184 0.10717841 0.10349628 0.09989275 0.09957281
  0.10113931 0.09323262 0.11007104 0.08793783]
 [0.12247808 0.09798463 0.09821172 0.08581256 0.10645735 0.09032994
  0.10095348 0.09713053 0.10073891 0.09990281]
 [0.10068969 0.09656123 0.09396787 0.10711435 0.10247035 0.10159823
  0.10918858 0.09762587 0.10294836 0.08783551]
 [0.10413533 0.10749564 0.1028861  0.10029841 0.10156565 0.09424046
  0.10174335 0.10342998 0.10243015 0.08177487]
 [0.10586838 0.10567959 0.09867364 0.09454779 0.09547344 0.09542162
  0.1034588  0.10676651 0.11208912 0.08202119]
 [0.09798576 0.08582627 0.08562905 0.09485276 0.11760915 0.08966827
  0.11170935 0.10972505 0.09647515 0.1105192 ]
 [0.113

...

INFO:tensorflow:global_step/sec: 47.5568
INFO:tensorflow:probabilities = [[0.00095501 0.5691663  0.29231825 0.08695259 0.00270023 0.01334744
  0.01450807 0.00587534 0.01366725 0.00050956]
 [0.00000396 0.00034197 0.00068815 0.99444854 0.0000078  0.00044205
  0.00000104 0.00014767 0.00307505 0.00084376]
 [0.00000034 0.05456536 0.9449296  0.00031691 0.         0.00000085
  0.0000102  0.00000004 0.00017674 0.        ]
 [0.0000016  0.00000001 0.00000432 0.00166101 0.00001    0.0002868
  0.00000003 0.0000052  0.99794763 0.00008335]
 [0.00001002 0.00000151 0.00004258 0.0000019  0.00028807 0.00002396
  0.99961    0.00000003 0.00002146 0.00000048]
 [0.00001345 0.00432507 0.00508564 0.00414207 0.00003323 0.00001981
  0.00000051 0.9786185  0.00050549 0.00725633]
 [0.0000002  0.00000305 0.00004312 0.00271133 0.5614127  0.00004303
  0.0000042  0.00047938 0.00288377 0.4324192 ]
 [0.         0.00000003 0.00008254 0.9999037  0.         0.00000091
  0.         0.00000008 0.00001276 0.00000001]
 [0.0000

INFO:tensorflow:loss = 0.07134671, step = 19900 (2.105 sec)
INFO:tensorflow:probabilities = [[0.00006093 0.00008489 0.00004665 0.00021983 0.00012065 0.99522924
  0.00023835 0.00004964 0.0038909  0.00005905]
 [0.00003281 0.00000024 0.0007445  0.00038503 0.00000499 0.00000788
  0.00000009 0.99682593 0.00007536 0.00192324]
 [0.0000101  0.00029361 0.00619636 0.986199   0.00000687 0.00113672
  0.00001428 0.00000229 0.0061375  0.00000333]
 [0.00004818 0.00000243 0.00092665 0.00028203 0.00003426 0.00002208
  0.00000012 0.9823627  0.00019223 0.01612938]
 [0.99948955 0.00000081 0.00007277 0.00012061 0.00000035 0.00016159
  0.0000077  0.00001138 0.00011673 0.00001854]
 [0.00004269 0.00000111 0.00077733 0.00000196 0.00169169 0.00002109
  0.9973531  0.00000072 0.00010613 0.00000418]
 [0.00001307 0.9987822  0.00054177 0.0000179  0.00002251 0.00003518
  0.00006566 0.00028971 0.00022972 0.00000224]
 [0.0000013  0.0000003  0.00001998 0.99940324 0.00000001 0.00004837
  0.00000001 0.00000004 0.00047536 

INFO:tensorflow:Saving checkpoints for 20000 into ./mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.16057704.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-03-31-05:22:29
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from ./mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-03-31-05:22:30
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9686, global_step = 20000, loss = 0.106510945
{'accuracy': 0.9686, 'loss': 0.106510945, 'global_step': 20000}


SystemExit: 

/usr/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
